In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2
import BCI_analysis
import os
import numpy as np
import matplotlib.pyplot as plt, mpld3
#mpld3.enable_notebook()





No module named 'cellpose'
cannot use anatomical mode, but otherwise suite2p will run normally


In [2]:
local_temp_dir = '/home/jupyter/temp/' 
metadata_dir = '/home/jupyter/bucket/Metadata/' 
raw_scanimage_dir_base ='/home/jupyter/bucket/Data/Calcium_imaging/raw/' 
suite2p_dir_base = '/home/jupyter/bucket/Data/Calcium_imaging/suite2p/'
bpod_path = '/home/jupyter/bucket/Data/Behavior/BCI_exported/'
setup = 'Bergamo-2P-Photostim'
sessionwise_path_base = "/home/jupyter/bucket/Data/Calcium_imaging/sessionwise_tba"

In [3]:
subject = 'BCI_35'
fov = 'FOV_05'
session = '072022'

session_dir = os.path.join(suite2p_dir_base,setup,subject,fov,session)
photostim_dir = os.path.join(session_dir,'photostim')
photostim_groups = np.load(os.path.join(photostim_dir,'photostim_groups.npy'),allow_pickle=True).tolist()

In [4]:
scalar_f0 = False

ops =  np.load(os.path.join(photostim_dir,'ops.npy'),allow_pickle = True).tolist()
F = np.load(os.path.join(photostim_dir,'F.npy'))
Fneu = np.load(os.path.join(photostim_dir,'Fneu.npy'))
F0_photostim = np.load(os.path.join(photostim_dir,'F0.npy'))
F0_scalar_photostim = np.nanmedian(F0_photostim,1)[:,np.newaxis]
F,Fneu = BCI_analysis.pipeline_imaging.remove_stim_artefacts(F,Fneu,ops['frames_per_file'])
photostim_indices = np.concatenate([[0],np.cumsum(ops['frames_per_file'])])[:-1]

if scalar_f0:
    dFF_photostim = (F-F0_scalar_photostim)/F0_scalar_photostim
else:
    dFF_photostim = (F-F0_photostim)/F0_photostim


ops =  np.load(os.path.join(session_dir,'ops.npy'),allow_pickle = True).tolist()
F = np.load(os.path.join(session_dir,'F.npy'))
Fneu = np.load(os.path.join(session_dir,'Fneu.npy'))
F0_session = np.load(os.path.join(session_dir,'F0.npy'))
F0_scalar_session = np.nanmedian(F0_session,1)[:,np.newaxis]
if scalar_f0:
    dFF_session = (F-F0_scalar_session)/F0_scalar_session
else:
    dFF_session = (F-F0_session)/F0_session



In [5]:
cell_idx = 0
fig = plt.figure(figsize = [8,6])
ax_session = fig.add_subplot(2,2,1)
ax_session.set_title('behavior')
ax_session_f0 = fig.add_subplot(2,2,2)
ax_session_f0.set_title('F0 - behavior')
ax_photostim = fig.add_subplot(2,2,3,sharex = ax_session,sharey = ax_session)
ax_photostim.set_title('photostim')
ax_photostim_f0 = fig.add_subplot(2,2,4,sharex = ax_session_f0,sharey = ax_session_f0)
ax_photostim_f0.set_title('F0 - photostim')

# ax_session.plot(dFF_session[cell_idx,:])
# ax_photostim.plot(dFF_photostim[cell_idx,:])
# ax_session_f0.plot(F0_session[cell_idx,:])
# ax_photostim_f0.plot(F0_photostim[cell_idx,:])

dff_session_maxed = dFF_session.copy()
dff_session_maxed[dff_session_maxed>10]=10
dff_session_maxed[dff_session_maxed<-3]=-3
dff_photostim_maxed = dFF_photostim.copy()
dff_photostim_maxed[dff_photostim_maxed>10]=10
dff_photostim_maxed[dff_photostim_maxed<-3]=-3

ax_session.plot(np.mean(dff_session_maxed,0))
ax_photostim.plot(np.mean(dff_photostim_maxed,0))
ax_session_f0.plot(np.mean(F0_session,0))
ax_photostim_f0.plot(np.mean(F0_photostim,0))

#ax_session.set_xlim([0,1000])
mpld3.display(fig)
# is the activity during photostim comparable to the activity during behavior??

In [6]:
fig = plt.figure(figsize = [8,8])
ax_f0_change = fig.add_subplot(2,2,1)
f0_diff = 100*(F0_scalar_photostim-F0_scalar_session)/F0_scalar_session
pctls = np.percentile(f0_diff,[1,99])
ax_f0_change.hist(f0_diff,np.arange(pctls[0],pctls[1],np.diff(pctls)/100))
ax_f0_change.set_title('scalar f0 change to photostim (dF/F0%)')
ax_f0_change.set_xlabel('F0_photostim - F0_session')



ax_dFF_change = fig.add_subplot(2,2,2)
dFF_diff = np.nanmean(dFF_photostim,1)-np.nanmean(dFF_session,1)
pctls = np.percentile(dFF_diff,[1,99])
ax_dFF_change.hist(dFF_diff,np.arange(pctls[0],pctls[1],np.diff(pctls)/100))
ax_dFF_change.set_xlabel('mean(dFF_photostim)-mean(dFF_session)')

ax_dFF_std_change = fig.add_subplot(2,2,4)
dFF_diff = np.nanstd(dFF_photostim,1)-np.nanstd(dFF_session,1)
pctls = np.percentile(dFF_diff,[1,99])
ax_dFF_std_change.hist(dFF_diff,np.arange(pctls[0],pctls[1],np.diff(pctls)/100))
ax_dFF_std_change.set_xlabel('std(dFF_photostim)-std(dFF_session)')

mpld3.display(fig)
# is the activity during photostim comparable to the activity during behavior??

In [7]:
pctls

array([-0.29259517,  0.14810267])